# Set up environment

In [1]:
#pip install pandas scipy matplotlib imageio cv2 opencv-python torch pyyaml tqdm torchvision seaborn

In [1]:
# import relevant libraries
from IPython.display import Image
import pandas as pd
import random
import os
import glob
import shutil
from scipy import ndimage
import matplotlib.pyplot as plt
import imageio
import json
import numpy as np
import cv2

In [2]:
%cd ../5_train_yolo_tooth_segmentation

C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation


In [3]:
# remote yolov5 folder
#!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5'

In [4]:
# clone repo
if os.path.exists('C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5/') == False:
    !git clone https://github.com/ultralytics/yolov5
    %cd yolov5
else:
    %cd yolov5
    !git init
    !git pull https://github.com/ultralytics/yolov5

C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\yolov5
Reinitialized existing Git repository in C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5/.git/
Updating f17c86b..7a39803
Fast-forward
 detect.py        |  4 ++--
 export.py        | 55 ++++++++++++++++++++++++++++++++++++++++++++++++++++++-
 models/common.py | 32 ++++++++++++++++++++++++++++----
 val.py           | 10 ++++++----
 4 files changed, 90 insertions(+), 11 deletions(-)


From https://github.com/ultralytics/yolov5
 * branch            HEAD       -> FETCH_HEAD


In [5]:
# install dependencies
if os.path.exists('C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/yolov5/') == False:
    !pip install -r yolov5/requirements.txt

In [6]:
import torch
print('Setup complete. Using torch %s %s' % (torch.__version__, torch.cuda.get_device_properties(0) if torch.cuda.is_available() else 'CPU'))

Setup complete. Using torch 1.9.1+cu102 _CudaDeviceProperties(name='Quadro RTX 8000', major=7, minor=5, total_memory=49152MB, multi_processor_count=72)


# Set up data

In [5]:
# remote data folder
!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data'
!rm -r 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/unseen_images'

In [7]:
# prepare data directory structure for Yolo
path = 'C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/'

if os.path.exists(path + 'data/') == False:
    os.mkdir(path + 'data/')
    os.mkdir(path + 'data/images/')
    os.mkdir(path + 'data/images/test')
    os.mkdir(path + 'data/images/train')
    os.mkdir(path + 'data/images/valid/')
    os.mkdir(path + 'data/labels/')
    os.mkdir(path + 'data/labels/test')
    os.mkdir(path + 'data/labels/train')
    os.mkdir(path + 'data/labels/valid/')
    os.mkdir(path + 'unseen_images/')

In [8]:
# define variables
path = 'C:/Users/dental-1/Documents/dent_seg/'
folder = '5_train_yolo_tooth_segmentation/'
bounding_boxes = os.listdir(path + folder + '/bounding_boxes2')
images_jpg = glob.glob(path + '2_dental_images/raw_images/*.jpg')
image_png = glob.glob(path + '2_dental_images/raw_images/*.png')
random.seed(1234)
norm = np.zeros((800,800))
image_names = []

for img in images_jpg:
    image_names.append(img.split('\\')[-1].split('.')[0])
    
for img in image_png:
    image_names.append(img.split('\\')[1][:-4])

In [9]:
# define function to organise data
def setup_data(bounding_boxes):   
    for bb in bounding_boxes:
        if 'cate' in bb:
            file_type = '.jpg'
        else:
            file_type = '.png'
        
        if bb.split('.txt')[0] in image_names:
            image_path = path + '2_dental_images/raw_images/' + bb.split('.txt')[0] + file_type
            source = path + folder + '/bounding_boxes2/' + bb
            # normalise image
            unnorm_img = imageio.imread(image_path, as_gray=True)
            normalized_img = cv2.normalize(unnorm_img, norm, 0, 255, cv2.NORM_MINMAX)
            if random.random() > 0.3:
                destination = path + folder + '/data/labels/train/' + bb
                shutil.copy(source, destination)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/train/' + bb.split('.txt')[0] + file_type, normalized_img)
            else:
                # assign test data to proper location
                destination_test = path + folder + '/data/labels/test/' + bb
                shutil.copy(source, destination_test)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/test/' + bb.split('.txt')[0] + file_type, normalized_img)
                # validation housekeeping
                destination_val = path + folder + '/data/labels/valid/' + bb
                shutil.copy(source, destination_val)
                # copy image to its respective folder
                cv2.imwrite(path + folder + '/data/images/valid/' + bb.split('.txt')[0] + file_type, normalized_img)
            image_names.remove(bb.split('.txt')[0]) 
    for image in image_names:
        if 'cate' in image:
            image_path = path + '2_dental_images/raw_images/' + image + '.jpg'
        else:
            image_path = path + '2_dental_images/raw_images/' + image + '.png'
        # normalise image
        unnorm_img = imageio.imread(image_path, as_gray=True)
        normalized_img = cv2.normalize(unnorm_img, norm, 0, 255, cv2.NORM_MINMAX)
        # copy image to its respective folder
        if 'cate' in image:
            cv2.imwrite(path + folder + '/unseen_images/' + image +'.jpg', normalized_img)
        else:
            cv2.imwrite(path + folder + '/unseen_images/' + image +'.png', normalized_img)

In [10]:
# populate folders
if len(os.listdir(path + folder + '/data/images/test')) <= 1:
    setup_data(bounding_boxes)

# Configure YAML files

In [11]:
with open('model_yaml', 'w+') as file:
    file.write(
        """
        # parameters
        nc: 1  # number of classes
        depth_multiple: 0.33  # model depth multiple
        width_multiple: 0.50  # layer channel multiple

        # anchors
        anchors:
          - [10,13, 16,30, 33,23]  # P3/8
          - [30,61, 62,45, 59,119]  # P4/16
          - [116,90, 156,198, 373,326]  # P5/32

        # YOLOv5 backbone
        backbone:
          # [from, number, module, args]
          [[-1, 1, Focus, [64, 3]],  # 0-P1/2
           [-1, 1, Conv, [128, 3, 2]],  # 1-P2/4
           [-1, 3, BottleneckCSP, [128]],
           [-1, 1, Conv, [256, 3, 2]],  # 3-P3/8
           [-1, 9, BottleneckCSP, [256]],
           [-1, 1, Conv, [512, 3, 2]],  # 5-P4/16
           [-1, 9, BottleneckCSP, [512]],
           [-1, 1, Conv, [1024, 3, 2]],  # 7-P5/32
           [-1, 1, SPP, [1024, [5, 9, 13]]],
           [-1, 3, BottleneckCSP, [1024, False]],  # 9
          ]

        # YOLOv5 head
        head:
          [[-1, 1, Conv, [512, 1, 1]],
           [-1, 1, nn.Upsample, [None, 2, 'nearest']],
           [[-1, 6], 1, Concat, [1]],  # cat backbone P4
           [-1, 3, BottleneckCSP, [512, False]],  # 13

           [-1, 1, Conv, [256, 1, 1]],
           [-1, 1, nn.Upsample, [None, 2, 'nearest']],
           [[-1, 4], 1, Concat, [1]],  # cat backbone P3
           [-1, 3, BottleneckCSP, [256, False]],  # 17 (P3/8-small)

           [-1, 1, Conv, [256, 3, 2]],
           [[-1, 14], 1, Concat, [1]],  # cat head P4
           [-1, 3, BottleneckCSP, [512, False]],  # 20 (P4/16-medium)

           [-1, 1, Conv, [512, 3, 2]],
           [[-1, 10], 1, Concat, [1]],  # cat head P5
           [-1, 3, BottleneckCSP, [1024, False]],  # 23 (P5/32-large)

           [[17, 20, 23], 1, Detect, [nc, anchors]],  # Detect(P3, P4, P5)
          ]
        """
    )

In [12]:
with open('data_yaml', 'w+') as file:
    file.write(
        """
        train: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/train
        val: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/valid
        test: C:/Users/dental-1/Documents/dent_seg/5_train_yolo_tooth_segmentation/data/images/test

        nc: 1
        names: ['tooth']
        """
    )

# Train model

In [7]:
%%time
!python train.py --batch 16 --epochs 1500 --data data_yaml --cfg model_yaml --weights ../../4_weights/IANN_initial_weight.pt --name teeth_detect --cache

github: up to date with https://github.com/ultralytics/yolov5 
Weights & Biases: run 'pip install wandb' to automatically track and visualize YOLOv5  runs (RECOMMENDED)
Wall time: 1h 29min 52s


train: weights=../../4_weights/IANN_initial_weight.pt, cfg=model_yaml, data=data_yaml, hyp=data\hyps\hyp.scratch.yaml, epochs=1500, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=runs\train, name=teeth_detect, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, patience=100, freeze=0, save_period=-1, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
From https://github.com/ultralytics/yolov5
   f17c86b..7a39803  master     -> origin/master
YOLOv5  v6.0-103-g7a39803 torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

hyperparameters: lr0=0.01, lrf=0.1, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_gamma=0.0, 

module 'signal' has no attribute 'SIGALRM'
Optimizer stripped from runs\train\teeth_detect4\weights\last.pt, 14.8MB
Optimizer stripped from runs\train\teeth_detect4\weights\best.pt, 14.8MB



val: Caching images (0.3GB ram): 100%|##########| 439/439 [00:01<00:00, 240.21it/s]

AutoAnchor: 5.57 anchors/target, 1.000 Best Possible Recall (BPR). Current anchors are a good fit to dataset 
Image sizes 640 train, 640 val
Using 8 dataloader workers
Logging results to runs\train\teeth_detect4
Starting training for 1500 epochs...

     Epoch   gpu_mem       box       obj       cls    labels  img_size

  0%|          | 0/71 [00:00<?, ?it/s]                                          C:\ProgramData\Anaconda3\envs\dental_project_of\lib\site-packages\torch\cuda\nccl.py:15: UserWarning: PyTorch is not compiled with NCCL support
  warnings.warn('PyTorch is not compiled with NCCL support')

    0/1499     1.87G    0.1091    0.3502         0       885       640:   0%|   
    0/1499     1.87G    0.1091    0.3502         0       885       640:   1%|1  C:\ProgramData\Anaconda3\envs\dental_project_of\lib\site-packages\torch\cuda\nccl.py:15: UserWarning: PyTorch is not compiled with NCCL support
 

    5/1499     2.63G   0.05969    0.1679         0       753       640:  46%|###
    5/1499     2.63G   0.05969    0.1679         0       753       640:  48%|###
    5/1499     2.63G   0.05957    0.1672         0       673       640:  48%|###
    5/1499     2.63G   0.05957    0.1672         0       673       640:  49%|###
    5/1499     2.63G   0.05954    0.1672         0       884       640:  49%|###
    5/1499     2.63G   0.05954    0.1672         0       884       640:  51%|###
    5/1499     2.63G   0.05946    0.1671         0       788       640:  51%|###
    5/1499     2.63G   0.05946    0.1671         0       788       640:  52%|###
    5/1499     2.63G   0.05948    0.1668         0       762       640:  52%|###
    5/1499     2.63G   0.05948    0.1668         0       762       640:  54%|###
    5/1499     2.63G   0.05944    0.1673         0       981       640:  54%|###
    5/1499     2.63G   0.05944    0.1673         0       981       640:  55%|###
    5/1499     2.63G   0.059

...

  431/1499     2.63G   0.03232   0.09408         0       730       640:  73%|###
  431/1499     2.63G   0.03232   0.09408         0       730       640:  75%|###
  431/1499     2.63G   0.03229   0.09417         0       803       640:  75%|###
  431/1499     2.63G   0.03229   0.09417         0       803       640:  76%|###
  431/1499     2.63G   0.03224   0.09413         0       741       640:  76%|###
  431/1499     2.63G   0.03224   0.09413         0       741       640:  77%|###
  431/1499     2.63G   0.03221   0.09406         0       736       640:  77%|###
  431/1499     2.63G   0.03221   0.09406         0       736       640:  79%|###
  431/1499     2.63G   0.03224   0.09415         0       871       640:  79%|###
  431/1499     2.63G   0.03224   0.09415         0       871       640:  80%|###
  431/1499     2.63G   0.03233   0.09435         0       978       640:  80%|###
  431/1499     2.63G   0.03233   0.09435         0       978       640:  82%|###
  431/1499     2.63G   0.032

  434/1499     2.63G   0.03205   0.09401         0       730       640:  77%|###
  434/1499     2.63G   0.03205   0.09401         0       730       640:  79%|###
  434/1499     2.63G   0.03205   0.09412         0       890       640:  79%|###
  434/1499     2.63G   0.03205   0.09412         0       890       640:  80%|###
  434/1499     2.63G   0.03203   0.09414         0       791       640:  80%|###
  434/1499     2.63G   0.03203   0.09414         0       791       640:  82%|###
  434/1499     2.63G   0.03199   0.09423         0       837       640:  82%|###
  434/1499     2.63G   0.03199   0.09423         0       837       640:  83%|###
  434/1499     2.63G   0.03195   0.09405         0       748       640:  83%|###
  434/1499     2.63G   0.03195   0.09405         0       748       640:  85%|###
  434/1499     2.63G   0.03198   0.09415         0       820       640:  85%|###
  434/1499     2.63G   0.03198   0.09415         0       820       640:  86%|###
  434/1499     2.63G   0.032

               Class     Images     Labels          P          R     mAP@.5 mAP@
               Class     Images     Labels          P          R     mAP@.5 mAP@
               Class     Images     Labels          P          R     mAP@.5 mAP@
               Class     Images     Labels          P          R     mAP@.5 mAP@
               Class     Images     Labels          P          R     mAP@.5 mAP@
                 all        439      11842      0.987      0.991      0.992      0.845

     Epoch   gpu_mem       box       obj       cls    labels  img_size

  0%|          | 0/71 [00:00<?, ?it/s]                                          
  453/1499     2.63G   0.03381    0.1062         0       982       640:   0%|   
  453/1499     2.63G   0.03381    0.1062         0       982       640:   1%|1  
  453/1499     2.63G   0.03344   0.09662         0       733       640:   1%|1  
  453/1499     2.63G   0.03344   0.09662         0       733       640:   3%|2  
  453/1499     2.63G   0.03268


     Epoch   gpu_mem       box       obj       cls    labels  img_size

  0%|          | 0/71 [00:00<?, ?it/s]                                          
  456/1499     2.63G   0.03153   0.08079         0       649       640:   0%|   
  456/1499     2.63G   0.03153   0.08079         0       649       640:   1%|1  
  456/1499     2.63G   0.03308   0.09331         0       942       640:   1%|1  
  456/1499     2.63G   0.03308   0.09331         0       942       640:   3%|2  
  456/1499     2.63G   0.03321   0.09202         0       740       640:   3%|2  
  456/1499     2.63G   0.03321   0.09202         0       740       640:   4%|4  
  456/1499     2.63G   0.03271   0.09432         0       871       640:   4%|4  
  456/1499     2.63G   0.03271   0.09432         0       871       640:   6%|5  
  456/1499     2.63G   0.03257   0.09467         0       826       640:   6%|5  
  456/1499     2.63G   0.03257   0.09467         0       826       640:   7%|7  
  456/1499     2.63G   0.03273   0.0

  474/1499     2.63G   0.03137   0.09071         0       729       640:  30%|##9
  474/1499     2.63G   0.03132   0.09017         0       636       640:  30%|##9
  474/1499     2.63G   0.03132   0.09017         0       636       640:  31%|###
  474/1499     2.63G   0.03124   0.09021         0       735       640:  31%|###
  474/1499     2.63G   0.03124   0.09021         0       735       640:  32%|###
  474/1499     2.63G   0.03108   0.08942         0       548       640:  32%|###
  474/1499     2.63G   0.03108   0.08942         0       548       640:  34%|###
  474/1499     2.63G   0.03118   0.08985         0       860       640:  34%|###
  474/1499     2.63G   0.03118   0.08985         0       860       640:  35%|###
  474/1499     2.63G   0.03113   0.08946         0       723       640:  35%|###
  474/1499     2.63G   0.03113   0.08946         0       723       640:  37%|###
  474/1499     2.63G   0.03116   0.08961         0       744       640:  37%|###
  474/1499     2.63G   0.031

# Test model

In [13]:
# run model again test image set
!python detect.py --weights runs/train/teeth_detect/weights/best.pt --img 416 --conf 0.4 --source ../data/images/test/ --save-txt --save-conf

detect: weights=['runs/train/teeth_detect/weights/best.pt'], source=../data/images/test/, imgsz=[416, 416], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-102-gf17c86b torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/439 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\data\images\test\1.2.840.114257.3.6.10028842080465500458430592052923973032886.png: 224x416 21 tooths, Done. (0.000s)
image 2/439 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\data\images\test\1.2.840.114257.3.6.10192418336062410458658248025036302706828.png: 256x416 26 tooths, Done. (0.000s)
ima

In [16]:
# run model against images in unseen image folder
!python detect.py --weights runs/train/teeth_detect/weights/best.pt --img 416 --conf 0.4 --source ../unseen_images/ --save-txt --save-conf

detect: weights=['runs/train/teeth_detect/weights/best.pt'], source=../unseen_images/, imgsz=[416, 416], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-92-ge80a09b torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 232 layers, 7246518 parameters, 0 gradients
image 1/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.1.1637304243952960394983328788351918369.png: 256x416 29 tooths, Done. (0.016s)
image 2/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.1.1637304243990896685435388404484448664.png: 256x416 29 tooths, Done. (0.000s)
image 3/1403 C:\Users\d

image 821/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.30812464304539330458630863012734517234561.png: 224x416 27 tooths, Done. (0.016s)
image 822/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.30848157872430380458613901000224761442331.png: 224x416 21 tooths, Done. (0.000s)
image 823/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.30853906832243250458659529009331670818712.png: 256x416 29 tooths, Done. (0.016s)
image 824/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.30854843376173890458411412094342900237959.png: 224x416 27 tooths, Done. (0.016s)
image 825/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.30860121920573160458512708094086467932633.png: 224x416 19 tooths, Done. (0.000s)
image 826/

image 995/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33010757904331160458561279037504241346185.png: 224x416 31 tooths, Done. (0.000s)
image 996/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33014659440040290458738430036944038406997.png: 224x416 28 tooths, Done. (0.016s)
image 997/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33015400384460090458515507208984473402628.png: 256x416 28 tooths, Done. (0.016s)
image 998/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\1.2.840.114257.3.6.33046354448204560458501119076482856212679.png: 224x416 30 tooths, Done. (0.016s)
image 999/1403 C:\Users\dental-1\Documents\dent_seg\5_train_yolo_tooth_segmentation\unseen_images\cate2-00001.jpg: 256x416 32 tooths, Done. (0.000s)
image 1000/1403 C:\Users\dental-1\Documents\dent_seg\5_trai

In [6]:
# run model against specific image
!python detect.py --weights ../../4_weights/IANN_fine_tuned_weight.pt --conf 0.4 --source ../../2_dental_images/raw_images/cate6-00022.jpg --name IANN_test --save-txt --save-conf

detect: weights=['../../4_weights/IANN_fine_tuned_weight.pt'], source=../../2_dental_images/raw_images/cate6-00022.jpg, imgsz=[640, 640], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=True, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs\detect, name=IANN_test, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False
YOLOv5  v6.0-102-gf17c86b torch 1.9.1+cu102 CUDA:0 (Quadro RTX 8000, 49152MiB)

Fusing layers... 
Model Summary: 224 layers, 7059304 parameters, 0 gradients
image 1/1 C:\Users\dental-1\Documents\dent_seg\2_dental_images\raw_images\cate6-00022.jpg: 384x640 17 molarss, 14 premolarss, 8 middles, Done. (0.016s)
Speed: 0.0ms pre-process, 15.6ms inference, 0.0ms NMS per image at shape (1, 3, 640, 640)
Results saved to runs\detect\IANN_test
1 labels saved to runs\detect\IANN_test\labels
